# Аналитика Taxi Data

## Импорт библиотек

#### Импорт Spark dependencies для подключения Spark

In [ ]:
import $ivy.`org.apache.spark::spark-sql:2.4.0`;

#### Импорт Vegas dependencies для визуализации с помощью Vegas

In [15]:
import $ivy.`org.vegas-viz::vegas:0.3.11`;
import $ivy.`org.vegas-viz::vegas-spark:0.3.11`;

Downloaded https://repo1.maven.org/maven2/org/vegas-viz/vegas_2.11/0.3.11/vegas_2.11-0.3.11.pom.sha1
Downloaded https://repo1.maven.org/maven2/org/vegas-viz/vegas_2.11/0.3.11/vegas_2.11-0.3.11.pom
Downloaded https://repo1.maven.org/maven2/org/webjars/bower/vega-lite/1.2.0/vega-lite-1.2.0.pom
Downloaded https://repo1.maven.org/maven2/io/circe/circe-parser_2.11/0.7.0/circe-parser_2.11-0.7.0.pom
Downloaded https://repo1.maven.org/maven2/io/circe/circe-core_2.11/0.7.0/circe-core_2.11-0.7.0.pom
Downloaded https://repo1.maven.org/maven2/org/scala-lang/scala-library/2.11.8/scala-library-2.11.8.pom
Downloaded https://repo1.maven.org/maven2/org/scala-lang/scala-library/2.11.8/scala-library-2.11.8.pom.sha1
Downloaded https://repo1.maven.org/maven2/io/circe/circe-core_2.11/0.7.0/circe-core_2.11-0.7.0.pom.sha1
Downloaded https://repo1.maven.org/maven2/com/github/julien-truffaut/monocle-core_2.11/1.1.0/monocle-core_2.11-1.1.0.pom
Downloaded https://repo1.maven.org/maven2/com/github/julien-truffaut/

import $ivy.$                            ;

import $ivy.$                                  ;

In [16]:
//Import Vegas plotting libraries
import vegas._
import vegas.render.WindowRenderer._
import vegas.sparkExt._

import vegas._

import vegas.render.WindowRenderer._

import vegas.sparkExt._

In [5]:
import org.apache.spark.sql.{DataFrame, SparkSession}
import org.apache.spark.sql.functions._
import org.apache.spark.sql.types._

import org.apache.spark.sql.{DataFrame, SparkSession}

import org.apache.spark.sql.functions._

import org.apache.spark.sql.types._

In [2]:
import org.apache.log4j.{Level, Logger};
Logger.getLogger("org").setLevel(Level.OFF);

import org.apache.log4j.{Level, Logger};


## Создание спарк-сессии

In [3]:
import org.apache.spark.sql._

val spark = SparkSession.
            builder().
            appName("Taxi_analysis").
            master("spark://spark-master:7077").
            config("spark.executor.memory", "512m").
            getOrCreate()

Using Spark's default log4j profile: org/apache/spark/log4j-defaults.properties


import org.apache.spark.sql._


spark: SparkSession = org.apache.spark.sql.SparkSession@70a9c4c0

## Создается Dataframe (читаем csv формат)

In [8]:
val path = "data/yellow_tripdata_2020-01.csv"

path: String = "data/yellow_tripdata_2020-01.csv"

In [6]:
val schema = StructType(Array(
      StructField("VendorID", IntegerType, true),
      StructField("tpep_pickup_datetime", TimestampType, true),
      StructField("tpep_dropoff_datetime", TimestampType, true),
      StructField("passenger_count", IntegerType, true),
      StructField("trip_distance", FloatType, true),
      StructField("RatecodeID", IntegerType, true),
      StructField("store_and_fwd_flag", StringType, true),
      StructField("PULocationID", IntegerType, true),
      StructField("DOLocationID", IntegerType, true),
      StructField("payment_type", IntegerType, true),
      StructField("fare_amount", FloatType, true),
      StructField("extra", FloatType, true),
      StructField("mta_tax", FloatType, true),
      StructField("tip_amount", FloatType, true),
      StructField("tolls_amount", FloatType, true),
      StructField("improvement_surcharge", FloatType, true),
      StructField("total_amount", FloatType, true),
      StructField("congestion_surcharge", FloatType, true)))

schema: StructType = List(
  StructField("VendorID", IntegerType, true, {}),
  StructField("tpep_pickup_datetime", TimestampType, true, {}),
  StructField("tpep_dropoff_datetime", TimestampType, true, {}),
  StructField("passenger_count", IntegerType, true, {}),
  StructField("trip_distance", FloatType, true, {}),
  StructField("RatecodeID", IntegerType, true, {}),
  StructField("store_and_fwd_flag", StringType, true, {}),
  StructField("PULocationID", IntegerType, true, {}),
  StructField("DOLocationID", IntegerType, true, {}),
  StructField("payment_type", IntegerType, true, {}),
  StructField("fare_amount", FloatType, true, {}),
  StructField("extra", FloatType, true, {}),
  StructField("mta_tax", FloatType, true, {}),
  StructField("tip_amount", FloatType, true, {}),
  StructField("tolls_amount", FloatType, true, {}),
  StructField("improvement_surcharge", FloatType, true, {}),
  StructField("total_amount", FloatType, true, {}),
  StructField("congestion_surcharge", FloatType, true

In [9]:
val Taxi_df = spark.read.format("csv").schema(schema).option("header", "true").load(path)

Taxi_df: DataFrame = [VendorID: int, tpep_pickup_datetime: timestamp ... 16 more fields]

In [10]:
Taxi_df.printSchema

root
 |-- VendorID: integer (nullable = true)
 |-- tpep_pickup_datetime: timestamp (nullable = true)
 |-- tpep_dropoff_datetime: timestamp (nullable = true)
 |-- passenger_count: integer (nullable = true)
 |-- trip_distance: float (nullable = true)
 |-- RatecodeID: integer (nullable = true)
 |-- store_and_fwd_flag: string (nullable = true)
 |-- PULocationID: integer (nullable = true)
 |-- DOLocationID: integer (nullable = true)
 |-- payment_type: integer (nullable = true)
 |-- fare_amount: float (nullable = true)
 |-- extra: float (nullable = true)
 |-- mta_tax: float (nullable = true)
 |-- tip_amount: float (nullable = true)
 |-- tolls_amount: float (nullable = true)
 |-- improvement_surcharge: float (nullable = true)
 |-- total_amount: float (nullable = true)
 |-- congestion_surcharge: float (nullable = true)



## Фильтрация данных

### Фильтрация состоит из:
* Удаление null-строк
* Выбор колонок, нужных для построения графиков

In [13]:
val filtered_df = Taxi_df.na.drop.select("passenger_count", "trip_distance", "tip_amount")

filtered_df: DataFrame = [passenger_count: int, trip_distance: float ... 1 more field]

**Вывод первых 40 строк итогового DataFrame**

In [14]:
filtered_df.show(40, false)

+---------------+-------------+----------+
|passenger_count|trip_distance|tip_amount|
+---------------+-------------+----------+
|1              |1.2          |1.47      |
|1              |1.2          |1.5       |
|1              |0.6          |1.0       |
|1              |0.8          |1.36      |
|1              |0.0          |0.0       |
|1              |0.03         |0.0       |
|1              |0.0          |0.01      |
|1              |0.0          |0.0       |
|4              |0.0          |0.0       |
|2              |0.7          |2.35      |
|2              |2.4          |1.75      |
|1              |0.8          |0.0       |
|1              |3.3          |4.15      |
|1              |1.07         |1.96      |
|1              |7.76         |4.84      |
|3              |1.6          |0.0       |
|1              |0.5          |1.0       |
|1              |1.7          |0.0       |
|1              |8.45         |0.0       |
|1              |0.0          |0.0       |
|1         

## Создание временного вида, чтобы можно было использовать SQL запрос

In [18]:
filtered_df.createOrReplaceTempView("data")

## Построение графика зависимости размера чаевых от кол-ва пассажиров

In [21]:
val graph1 = Vegas("Graphic tip amount from amount of passengers", width = 500.0, height = 500.0)
  .withDataFrame(spark.sql("select passenger_count, tip_amount from data"))
  .mark(Point)
  .encodeX("passenger_count", Quant)
  .encodeY("tip_amount", Quant)

graph1: DSL.ExtendedUnitSpecBuilder = ExtendedUnitSpecBuilder(
  ExtendedUnitSpec(
    Some(500.0),
    Some(500.0),
    Point,
    Some(
      Encoding(
        None,
        None,
        Some(
          PositionChannelDef(
            None,
            None,
            None,
            Some("passenger_count"),
            Some(Quantitative),
            None,
            None,
            None,
            None,
            None
          )
        ),
        Some(
          PositionChannelDef(
            None,
            None,
            None,
            Some("tip_amount"),
            Some(Quantitative),
            None,
            None,
            None,
            None,
            None
          )
        ),
        None,
        None,
...

In [22]:
graph1.show

<iframe id="frame-vegas-5b24add0-7488-452d-b6f0-9ef694fd5a1f" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-5b24add0-7488-452d-b6f0-9ef694fd5a1f'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "width" : 500.0,
 "height" : 500.0,
 "mark" : "point",
 "encoding" : {
 "x" : {
 "field" : "passenger_count",
 "type" : "quantitative"
 },
 "y" : {
 "field" : "tip_amount",
 "type" : "quantitative"
 }
 },
 "description" : "Graphic tip amount from amount of passengers",
 "data" : {
 "values" : [
 {
 "passenger_count" : 1,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 1.0
 },
 {
 "passenger_count" : 5,
 "tip_amount" : 5.579999923706055
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 2.259999990463257
 },
 {
 "passenger_count" : 2,
 "tip_amount" : 5.199999809265137
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 2,
 "tip_amount" : 3.1500000953674316
 },
 {
 "passenger_count" : 6,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 3.059999942779541
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 4.559999942779541
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 1.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 1.9500000476837158
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 2,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 2,
 "tip_amount" : 3.0
 },
 {
 "passenger_count" : 2,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 4.960000038146973
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 2.1600000858306885
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 2,
 "tip_amount" : 3.259999990463257
 },
 {
 "passenger_count" : 3,
 "tip_amount" : 3.1500000953674316
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 6,
 "tip_amount" : 3.259999990463257
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 3.259999990463257
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 3.319999933242798
 },
 {
 "passenger_count" : 2,
 "tip_amount" : 3.319999933242798
 },
 {
 "passenger_count" : 4,
 "tip_amount" : 2.3499999046325684
 },
 {
 "passenger_count" : 2,
 "tip_amount" : 3.450000047683716
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 1.5
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 1.7599999904632568
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 3.359999895095825
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 2.359999895095825
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 2.1600000858306885
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 0.800000011920929
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 3.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 1.8600000143051147
 },
 {
 "passenger_count" : 3,
 "tip_amount" : 3.450000047683716
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 1.559999942779541
 },
 {
 "passenger_count" : 4,
 "tip_amount" : 2.859999895095825
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 4.059999942779541
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 4.0
 },
 {
 "passenger_count" : 1,
 "tip_amount" : 1.0
 },
 {
 "passenger_count" : 2,
 "tip_amount" : 0.0
 },
 {
 "passenger_count" : 

## Построение графика зависимости размера чаевых от пройденного расстояния

In [23]:
val graph2 = Vegas("Graphic tip amount from trip distance", width = 500.0, height = 500.0)
  .withDataFrame(spark.sql("select trip_distance, tip_amount from data"))
  .mark(Bar)
  .encodeX("trip_distance", Quant)
  .encodeY("tip_amount", Quant)

graph2: DSL.ExtendedUnitSpecBuilder = ExtendedUnitSpecBuilder(
  ExtendedUnitSpec(
    Some(500.0),
    Some(500.0),
    Bar,
    Some(
      Encoding(
        None,
        None,
        Some(
          PositionChannelDef(
            None,
            None,
            None,
            Some("trip_distance"),
            Some(Quantitative),
            None,
            None,
            None,
            None,
            None
          )
        ),
        Some(
          PositionChannelDef(
            None,
            None,
            None,
            Some("tip_amount"),
            Some(Quantitative),
            None,
            None,
            None,
            None,
            None
          )
        ),
        None,
        None,
...

In [24]:
graph2.show

<iframe id="frame-vegas-ccf0f650-af3a-4eca-9e5f-25f17c46f5fe" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-ccf0f650-af3a-4eca-9e5f-25f17c46f5fe'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "width" : 500.0,
 "height" : 500.0,
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "trip_distance",
 "type" : "quantitative"
 },
 "y" : {
 "field" : "tip_amount",
 "type" : "quantitative"
 }
 },
 "description" : "Graphic tip amount from trip distance",
 "data" : {
 "values" : [
 {
 "trip_distance" : 5.199999809265137,
 "tip_amount" : 5.75
 },
 {
 "trip_distance" : 0.8999999761581421,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 1.2599999904632568,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 1.25,
 "tip_amount" : 4.559999942779541
 },
 {
 "trip_distance" : 3.619999885559082,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 2.7899999618530273,
 "tip_amount" : 3.859999895095825
 },
 {
 "trip_distance" : 1.559999942779541,
 "tip_amount" : 3.390000104904175
 },
 {
 "trip_distance" : 8.470000267028809,
 "tip_amount" : 5.860000133514404
 },
 {
 "trip_distance" : 2.299999952316284,
 "tip_amount" : 2.859999895095825
 },
 {
 "trip_distance" : 1.9600000381469727,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 1.0099999904632568,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 1.0299999713897705,
 "tip_amount" : 2.1600000858306885
 },
 {
 "trip_distance" : 2.9000000953674316,
 "tip_amount" : 1.0
 },
 {
 "trip_distance" : 7.25,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 0.6200000047683716,
 "tip_amount" : 1.100000023841858
 },
 {
 "trip_distance" : 3.180000066757202,
 "tip_amount" : 3.859999895095825
 },
 {
 "trip_distance" : 6.0,
 "tip_amount" : 5.159999847412109
 },
 {
 "trip_distance" : 1.7200000286102295,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 0.8500000238418579,
 "tip_amount" : 2.319999933242798
 },
 {
 "trip_distance" : 1.4500000476837158,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 2.819999933242798,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 5.369999885559082,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 0.4000000059604645,
 "tip_amount" : 1.4500000476837158
 },
 {
 "trip_distance" : 2.2300000190734863,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 1.0800000429153442,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 3.700000047683716,
 "tip_amount" : 8.0
 },
 {
 "trip_distance" : 2.119999885559082,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 18.940000534057617,
 "tip_amount" : 20.559999465942383
 },
 {
 "trip_distance" : 1.0,
 "tip_amount" : 1.9500000476837158
 },
 {
 "trip_distance" : 0.7900000214576721,
 "tip_amount" : 2.0
 },
 {
 "trip_distance" : 4.539999961853027,
 "tip_amount" : 3.0
 },
 {
 "trip_distance" : 3.5899999141693115,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 3.0999999046325684,
 "tip_amount" : 3.6600000858306885
 },
 {
 "trip_distance" : 2.0999999046325684,
 "tip_amount" : 2.0
 },
 {
 "trip_distance" : 0.8500000238418579,
 "tip_amount" : 1.0
 },
 {
 "trip_distance" : 5.630000114440918,
 "tip_amount" : 4.760000228881836
 },
 {
 "trip_distance" : 1.7000000476837158,
 "tip_amount" : 1.0
 },
 {
 "trip_distance" : 0.8600000143051147,
 "tip_amount" : 1.0
 },
 {
 "trip_distance" : 3.25,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 1.0199999809265137,
 "tip_amount" : 2.7899999618530273
 },
 {
 "trip_distance" : 1.3600000143051147,
 "tip_amount" : 1.0
 },
 {
 "trip_distance" : 1.600000023841858,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 1.399999976158142,
 "tip_amount

### Ограничиваю интервал значений оси Ox и оси Oy для лучшего отображения графика

In [36]:
val graph3 = Vegas("Graphic tip amount from trip distance", width = 500.0, height = 500.0)
  .withDataFrame(spark.sql("select trip_distance, tip_amount from data where (trip_distance <= 30) and (tip_amount < 35)"))
  .mark(Bar)
  .encodeX("trip_distance", Quant)
  .encodeY("tip_amount", Quant)

graph3: DSL.ExtendedUnitSpecBuilder = ExtendedUnitSpecBuilder(
  ExtendedUnitSpec(
    Some(500.0),
    Some(500.0),
    Bar,
    Some(
      Encoding(
        None,
        None,
        Some(
          PositionChannelDef(
            None,
            None,
            None,
            Some("trip_distance"),
            Some(Quantitative),
            None,
            None,
            None,
            None,
            None
          )
        ),
        Some(
          PositionChannelDef(
            None,
            None,
            None,
            Some("tip_amount"),
            Some(Quantitative),
            None,
            None,
            None,
            None,
            None
          )
        ),
        None,
        None,
...

In [37]:
graph3.show

<iframe id="frame-vegas-2a3c94f0-eee9-4345-9f07-0334d7a56d56" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-2a3c94f0-eee9-4345-9f07-0334d7a56d56'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "width" : 500.0,
 "height" : 500.0,
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "trip_distance",
 "type" : "quantitative"
 },
 "y" : {
 "field" : "tip_amount",
 "type" : "quantitative"
 }
 },
 "description" : "Graphic tip amount from trip distance",
 "data" : {
 "values" : [
 {
 "trip_distance" : 15.6899995803833,
 "tip_amount" : 10.279999732971191
 },
 {
 "trip_distance" : 0.5299999713897705,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 0.8199999928474426,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 0.7300000190734863,
 "tip_amount" : 2.559999942779541
 },
 {
 "trip_distance" : 3.2899999618530273,
 "tip_amount" : 3.059999942779541
 },
 {
 "trip_distance" : 1.600000023841858,
 "tip_amount" : 2.569999933242798
 },
 {
 "trip_distance" : 1.5199999809265137,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 0.5400000214576721,
 "tip_amount" : 1.659999966621399
 },
 {
 "trip_distance" : 0.3199999928474426,
 "tip_amount" : 1.0
 },
 {
 "trip_distance" : 4.28000020980835,
 "tip_amount" : 3.859999895095825
 },
 {
 "trip_distance" : 12.239999771118164,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 3.4800000190734863,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 3.319999933242798,
 "tip_amount" : 4.659999847412109
 },
 {
 "trip_distance" : 1.9700000286102295,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 1.0399999618530273,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 9.859999656677246,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 1.840000033378601,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 0.2800000011920929,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 1.309999942779541,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 3.7899999618530273,
 "tip_amount" : 3.359999895095825
 },
 {
 "trip_distance" : 1.059999942779541,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 2.869999885559082,
 "tip_amount" : 3.059999942779541
 },
 {
 "trip_distance" : 0.3700000047683716,
 "tip_amount" : 1.0
 },
 {
 "trip_distance" : 6.460000038146973,
 "tip_amount" : 3.5
 },
 {
 "trip_distance" : 0.8799999952316284,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 7.980000019073486,
 "tip_amount" : 2.5
 },
 {
 "trip_distance" : 7.730000019073486,
 "tip_amount" : 6.059999942779541
 },
 {
 "trip_distance" : 3.4000000953674316,
 "tip_amount" : 3.450000047683716
 },
 {
 "trip_distance" : 2.4000000953674316,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 5.199999809265137,
 "tip_amount" : 4.449999809265137
 },
 {
 "trip_distance" : 6.119999885559082,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 6.449999809265137,
 "tip_amount" : 5.949999809265137
 },
 {
 "trip_distance" : 1.340000033378601,
 "tip_amount" : 2.259999990463257
 },
 {
 "trip_distance" : 2.7899999618530273,
 "tip_amount" : 2.9600000381469727
 },
 {
 "trip_distance" : 2.0199999809265137,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 3.8399999141693115,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 2.140000104904175,
 "tip_amount" : 5.489999771118164
 },
 {
 "trip_distance" : 0.6000000238418579,
 "tip_amount" : 0.0
 },
 {
 "trip_distance" : 1.2000000476837158,
 "tip_amount" : 2.1600000858306885
 },
 {
 "trip_distance" : 2.7799999713897705,
 "tip_amount" : 3.4600000381469727
 },
 {
 "trip_distance" : 8.600000381469727,
 "tip_amount" : 6.75
 },
 {
 "trip_distance" : 0.0,
 

## Вывод

**Из графика зависимости размера чаевых от кол-ва пассажиров следует, что:**
 * Самые большие чаевые давала первая группа пассажиров (1 человек)
 * Чаще всего чаевые давала первая группа пассажиров, реже всего 3 группа и 4 группа (именно где 4 пассажира)
 * В среднем можно предположить, что первая и вторая группа пассажиров самые благоприятные в плане чаевых

**Из графика зависимости размера чаевых от пройденного расстояния следует, что:**
 * Не учитывая выброс (чаевые ~ 255 при расстоянии 0), то наибольшие чаевые получали при расстоянии 16-19 миль
 * Минимальные чаевые при расстоянии 2-4 мили
 * В итоге можно предположить, что лучше брать заказ на расстояние 7-10 миль или 15-20 миль, если нужны хорошие чаевые